In [11]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout
from keras.callbacks import EarlyStopping
from keras.optimizers import Adam
from tensorflow.keras.losses import Huber
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

In [2]:
df = pd.read_csv("cleaned.csv")
df.isna().sum()

Unnamed: 0                           0
Country                              0
Year                                 0
Energy supply adequacy (%)           0
Protein supply (g/cap/day)           0
Animal protein supply (g/cap/day)    0
Cereal import dependency (%)         0
Energy supply (kcal/cap/day)         0
Undernourishment (%)                 0
Energy from cereals (%)              0
dtype: int64

In [3]:
# Relevant columns for training
features = [
    'Energy supply adequacy (%)',
    'Protein supply (g/cap/day)',
    'Animal protein supply (g/cap/day)',
    'Cereal import dependency (%)',
    'Energy supply (kcal/cap/day)',
    'Energy from cereals (%)'
]
target = 'Undernourishment (%)'

# Define time steps (using the last 3 years to predict the next year)
time_steps = 3

# To store predictions for each country
predictions_by_country = {}

In [4]:
# Group the dataframe by 'Country'
for country, country_df in df.groupby('Country'):
    try:
        # Normalize the data (independently for each country)
        scaler = MinMaxScaler()
        df_scaled = scaler.fit_transform(country_df[features + [target]])

        # Create sequences (sliding windows) of the last `time_steps` years
        def create_sequences(data, time_steps):
            x, y = [], []
            for i in range(len(data) - time_steps):
                x.append(data[i:i + time_steps, :-1])  # All features except the target
                y.append(data[i + time_steps, -1])  # The target (Undernourishment)
            return np.array(x), np.array(y)

        # Create training data for the country
        X, y = create_sequences(df_scaled, time_steps)

        # Build the LSTM model
        model = Sequential()
        model.add(LSTM(units=100, return_sequences=True, input_shape=(X.shape[1], X.shape[2])))
        model.add(Dropout(0.2))  # Dropout layer to prevent overfitting
        model.add(LSTM(units=100, return_sequences=True))
        model.add(Dropout(0.2))  # Another dropout layer
        model.add(LSTM(units=50))  # Final LSTM layer
        model.add(Dense(1))  # Output layer to predict the undernourishment percentage

        # Compile the model
        model.compile(optimizer='adam', loss='mean_squared_error')

        # Early stopping to prevent overfitting
        early_stopping = EarlyStopping(monitor='val_loss', patience=10)

        # Train the model on the country's data with a validation split
        model.fit(X, y, epochs=100, batch_size=32, validation_split=0.2, callbacks=[early_stopping])

        # Predict the future undernourishment percentages for 2023, 2024, and 2025
        future_predictions = []
        current_input = df_scaled[-time_steps:, :-1].reshape(1, time_steps, len(features))  # Reshape for LSTM input

        for _ in range(3):  # Predict for 3 years
            predicted_undernourishment = model.predict(current_input)

            # Inverse transform the prediction (only for the target column)
            predicted_undernourishment = scaler.inverse_transform(
                np.hstack([np.zeros((1, len(features))), predicted_undernourishment])
            )[:, -1]

            future_predictions.append(predicted_undernourishment[0])

            # Prepare the input for the next prediction
            predicted_value = np.zeros((1, 1, len(features)))  # Create an array of zeros
            predicted_value[0, 0, 0] = predicted_undernourishment  # Place the predicted value

            # Shift the input and append the predicted value
            current_input = np.append(current_input[:, 1:, :], predicted_value, axis=1)

        # Store predictions for the current country
        predictions_by_country[country] = future_predictions

    except Exception as e:
        print(f"Error processing country {country}: {e}")


c:\Users\LENOVO\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - loss: 0.1096 - val_loss: 0.1147
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step - loss: 0.1015 - val_loss: 0.1000
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 65ms/step - loss: 0.0938 - val_loss: 0.0857
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - loss: 0.0864 - val_loss: 0.0717
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - loss: 0.0805 - val_loss: 0.0583
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step - loss: 0.0732 - val_loss: 0.0460
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.0688 - val_loss: 0.0352
Epoch 8/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step - loss: 0.0638 - val_loss: 0.0266
Epoch 9/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - loss: 0.0634 - val_loss: 0.0204
Epoch 10/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.0605 - val_loss: 0.0164
Epoch 11/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step - loss: 0.0603 - val_loss: 0.0144
Epoch 12/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step - loss: 0.0552 - val_loss

c:\Users\LENOVO\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - loss: 0.3100 - val_loss: 9.0191e-04
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.2966 - val_loss: 3.2126e-04
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.2842 - val_loss: 7.1590e-04
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step - loss: 0.2711 - val_loss: 0.0022
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step - loss: 0.2588 - val_loss: 0.0052
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - loss: 0.2448 - val_loss: 0.0101
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.2325 - val_loss: 0.0173
Epoch 8/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.2188 - val_loss: 0.0275
Epoch 9/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step - loss: 0.2036 - val_loss: 0.0412
Epoch 10/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - loss: 0.1948 - val_loss: 0.0586
Epoch 11/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step - loss: 0.1783 - val_loss: 0.0803
Epoch 12/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - loss: 0.1685 - val_loss

c:\Users\LENOVO\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


...

1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - loss: 0.2510 - val_loss: 0.5913
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - loss: 0.2323 - val_loss: 0.5605
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.2121 - val_loss: 0.5283
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step - loss: 0.1951 - val_loss: 0.4943
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - loss: 0.1793 - val_loss: 0.4578
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.1589 - val_loss: 0.4186
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.1437 - val_loss: 0.3765
Epoch 8/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.1303 - val_loss: 0.3316
Epoch 9/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step - loss: 0.1156 - val_loss: 0.2852
Epoch 10/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step - loss: 0.1116 - val_loss: 0.2408
Epoch 11/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step - loss: 0.1153 - val_loss: 0.2054
Epoch 12/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - loss: 0.1140 - val_loss: 0.1837
Epo

c:\Users\LENOVO\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - loss: 0.3948 - val_loss: 0.0195
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.3744 - val_loss: 0.0148
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step - loss: 0.3563 - val_loss: 0.0108
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step - loss: 0.3359 - val_loss: 0.0079
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step - loss: 0.3127 - val_loss: 0.0063
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step - loss: 0.2863 - val_loss: 0.0068
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.2655 - val_loss: 0.0106
Epoch 8/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 81ms/step - loss: 0.2384 - val_loss: 0.0195
Epoch 9/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step - loss: 0.2036 - val_loss: 0.0359
Epoch 10/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - loss: 0.1792 - val_loss: 0.0621
Epoch 11/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.1557 - val_loss: 0.0997
Epoch 12/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step - loss: 0.1309 - val_loss: 0.1494
Epo

c:\Users\LENOVO\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - loss: 0.1897 - val_loss: 0.9059
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.1756 - val_loss: 0.8658
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step - loss: 0.1605 - val_loss: 0.8248
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - loss: 0.1491 - val_loss: 0.7821
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step - loss: 0.1324 - val_loss: 0.7365
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.1212 - val_loss: 0.6873
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 86ms/step - loss: 0.1092 - val_loss: 0.6339
Epoch 8/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.0965 - val_loss: 0.5761
Epoch 9/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - loss: 0.0857 - val_loss: 0.5146
Epoch 10/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - loss: 0.0798 - val_loss: 0.4519
Epoch 11/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - loss: 0.0777 - val_loss: 0.3944
Epoch 12/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 86ms/step - loss: 0.0797 - val_loss: 0.3503
Epo

In [5]:
# Output the predictions for each country for the years 2023, 2024, and 2025
for country, predictions in predictions_by_country.items():
    print(f"Country: {country}, Predicted Undernourishment for 2023: {predictions[0]}, 2024: {predictions[1]}, 2025: {predictions[2]}")

Country: Afghanistan, Predicted Undernourishment for 2023: 21.048968983441593, 2024: 18.83457106612623, 2025: 14.243488602340223
Country: Albania, Predicted Undernourishment for 2023: 5.855641439557076, 2024: 5.711057719588281, 2025: 5.442934674024583
Country: Algeria, Predicted Undernourishment for 2023: 4.586330205202103, 2024: 4.267478287220001, 2025: 3.634869083762169
Country: Angola, Predicted Undernourishment for 2023: 28.395927524566652, 2024: 23.431403732299806, 2025: 16.25092113018036
Country: Argentina, Predicted Undernourishment for 2023: 3.530445265769958, 2024: 3.4718835234642023, 2025: 3.3629864633083337
Country: Armenia, Predicted Undernourishment for 2023: 5.184487095475197, 2024: 4.301485648751259, 2025: 2.8003714865073563
Country: Australia, Predicted Undernourishment for 2023: 2.499709806550527, 2024: 2.4988749431213364, 2025: 2.497856151079759
Country: Austria, Predicted Undernourishment for 2023: 2.499037998204585, 2024: 2.4978814015630633, 2025: 2.4961033107247204

In [6]:
# Initialize lists to store true and predicted values
all_true_values = []
all_predictions = []

# Group the dataframe by 'Country' for evaluation
for country, country_df in df.groupby('Country'):
    # Store true values for comparison (assuming these are the last 3 actual values)
    true_values = country_df[target].values[-3:]  # Last 3 years for true values
    all_true_values.extend(true_values)  # Add true values to the list
    all_predictions.extend(predictions_by_country[country])  # Add predictions to the list

In [7]:
# Calculate metrics
mae = mean_absolute_error(all_true_values, all_predictions)
mse = mean_squared_error(all_true_values, all_predictions)
rmse = np.sqrt(mse)
r2 = r2_score(all_true_values, all_predictions)

# Display the overall metrics
print(f"Overall Metrics: MAE: {mae:.4f}, MSE: {mse:.4f}, RMSE: {rmse:.4f}, R²: {r2:.4f}")

Overall Metrics: MAE: 3.3192, MSE: 29.4126, RMSE: 5.4233, R²: 0.7399


In [8]:
# Calculate and display metrics for each year
true_2023, true_2024, true_2025 = all_true_values[::3], all_true_values[1::3], all_true_values[2::3]
pred_2023, pred_2024, pred_2025 = all_predictions[::3], all_predictions[1::3], all_predictions[2::3]

# Metrics for 2023
mae_2023 = mean_absolute_error(true_2023, pred_2023)
mse_2023 = mean_squared_error(true_2023, pred_2023)
rmse_2023 = np.sqrt(mse_2023)
r2_2023 = r2_score(true_2023, pred_2023)

# Metrics for 2024
mae_2024 = mean_absolute_error(true_2024, pred_2024)
mse_2024 = mean_squared_error(true_2024, pred_2024)
rmse_2024 = np.sqrt(mse_2024)
r2_2024 = r2_score(true_2024, pred_2024)

# Metrics for 2025
mae_2025 = mean_absolute_error(true_2025, pred_2025)
mse_2025 = mean_squared_error(true_2025, pred_2025)
rmse_2025 = np.sqrt(mse_2025)
r2_2025 = r2_score(true_2025, pred_2025)

# Display metrics for each year
print(f"Metrics for 2023: MAE: {mae_2023:.4f}, MSE: {mse_2023:.4f}, RMSE: {rmse_2023:.4f}, R²: {r2_2023:.4f}")
print(f"Metrics for 2024: MAE: {mae_2024:.4f}, MSE: {mse_2024:.4f}, RMSE: {rmse_2024:.4f}, R²: {r2_2024:.4f}")
print(f"Metrics for 2025: MAE: {mae_2025:.4f}, MSE: {mse_2025:.4f}, RMSE: {rmse_2025:.4f}, R²: {r2_2025:.4f}")

Metrics for 2023: MAE: 2.9285, MSE: 21.3192, RMSE: 4.6173, R²: 0.8017
Metrics for 2024: MAE: 3.2372, MSE: 26.3833, RMSE: 5.1365, R²: 0.7666
Metrics for 2025: MAE: 3.7919, MSE: 40.5353, RMSE: 6.3667, R²: 0.6581


In [15]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout
from keras.callbacks import EarlyStopping
from keras.optimizers import Adam
from tensorflow.keras.losses import Huber
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf

# Load dataset
df = pd.read_csv("cleaned.csv")
df.isna().sum()

# Relevant columns for training
features = [
    'Energy supply adequacy (%)',
    'Protein supply (g/cap/day)',
    'Animal protein supply (g/cap/day)',
    'Cereal import dependency (%)',
    'Energy supply (kcal/cap/day)',
    'Energy from cereals (%)'
]
target = 'Undernourishment (%)'

# Define time steps (using the last 5 years to predict the next year)
time_steps = 5

# To store predictions for each country
predictions_by_country = {}

# Group the dataframe by 'Country'
for country, country_df in df.groupby('Country'):
    try:
        # Normalize the data (independently for each country)
        scaler = MinMaxScaler()
        df_scaled = scaler.fit_transform(country_df[features + [target]])

        # Create sequences (sliding windows) of the last `time_steps` years
        def create_sequences(data, time_steps):
            x, y = [], []
            for i in range(len(data) - time_steps):
                x.append(data[i:i + time_steps, :-1])  # All features except the target
                y.append(data[i + time_steps, -1])  # The target (Undernourishment)
            return np.array(x), np.array(y)

        # Create training data for the country
        X, y = create_sequences(df_scaled, time_steps)

        # Build the LSTM model
        model = Sequential()
        model.add(tf.keras.Input(shape=(X.shape[1], X.shape[2])))  # Correct input shape specification
        model.add(LSTM(units=150, return_sequences=True))
        model.add(Dropout(0.3))  # Dropout layer to prevent overfitting
        model.add(LSTM(units=150, return_sequences=True))
        model.add(Dropout(0.3))  # Another dropout layer
        model.add(LSTM(units=75))  # Final LSTM layer
        model.add(Dense(50, activation='relu', kernel_regularizer='l2'))  # Dense layer with L2 regularization
        model.add(Dense(1))  # Output layer to predict the undernourishment percentage

        # Compile the model with Huber Loss and a reduced learning rate
        optimizer = Adam(learning_rate=0.0001)
        huber_loss = Huber()  # Use the Huber loss function correctly
        model.compile(optimizer=optimizer, loss=huber_loss)

        # Early stopping to prevent overfitting
        early_stopping = EarlyStopping(monitor='val_loss', patience=10)

        # Train the model on the country's data with a validation split
        model.fit(X, y, epochs=200, batch_size=32, validation_split=0.2, callbacks=[early_stopping])

        # Predict the future undernourishment percentages for 2023, 2024, and 2025
        future_predictions = []
        current_input = df_scaled[-time_steps:, :-1].reshape(1, time_steps, len(features))  # Reshape for LSTM input

        for _ in range(3):  # Predict for 3 years
            predicted_undernourishment = model.predict(current_input)

            # Inverse transform the prediction (only for the target column)
            predicted_undernourishment = scaler.inverse_transform(
                np.hstack([np.zeros((1, len(features))), predicted_undernourishment])
            )[:, -1]

            future_predictions.append(predicted_undernourishment[0])

            # Prepare the input for the next prediction
            predicted_value = np.zeros((1, 1, len(features)))  # Create an array of zeros
            predicted_value[0, 0, 0] = predicted_undernourishment  # Place the predicted value

            # Shift the input and append the predicted value
            current_input = np.append(current_input[:, 1:, :], predicted_value, axis=1)

        # Store predictions for the current country
        predictions_by_country[country] = future_predictions

    except Exception as e:
        print(f"Error processing country {country}: {e}")

# Output the predictions for each country for the years 2023, 2024, and 2025
for country, predictions in predictions_by_country.items():
    print(f"Country: {country}, Predicted Undernourishment for 2023: {predictions[0]}, 2024: {predictions[1]}, 2025: {predictions[2]}")

# Initialize lists to store true and predicted values
all_true_values = []
all_predictions = []

# Group the dataframe by 'Country' for evaluation
for country, country_df in df.groupby('Country'):
    # Store true values for comparison (assuming these are the last 3 actual values)
    true_values = country_df[target].values[-3:]  # Last 3 years for true values
    all_true_values.extend(true_values)  # Add true values to the list
    all_predictions.extend(predictions_by_country[country])  # Add predictions to the list

# Calculate metrics
mae = mean_absolute_error(all_true_values, all_predictions)
mse = mean_squared_error(all_true_values, all_predictions)
rmse = np.sqrt(mse)
r2 = r2_score(all_true_values, all_predictions)

# Display the overall metrics
print(f"Overall Metrics: MAE: {mae:.4f}, MSE: {mse:.4f}, RMSE: {rmse:.4f}, R²: {r2:.4f}")

# Calculate and display metrics for each year
true_2023, true_2024, true_2025 = all_true_values[::3], all_true_values[1::3], all_true_values[2::3]
pred_2023, pred_2024, pred_2025 = all_predictions[::3], all_predictions[1::3], all_predictions[2::3]

# Metrics for 2023
mae_2023 = mean_absolute_error(true_2023, pred_2023)
mse_2023 = mean_squared_error(true_2023, pred_2023)
rmse_2023 = np.sqrt(mse_2023)
r2_2023 = r2_score(true_2023, pred_2023)

# Metrics for 2024
mae_2024 = mean_absolute_error(true_2024, pred_2024)
mse_2024 = mean_squared_error(true_2024, pred_2024)
rmse_2024 = np.sqrt(mse_2024)
r2_2024 = r2_score(true_2024, pred_2024)

# Metrics for 2025
mae_2025 = mean_absolute_error(true_2025, pred_2025)
mse_2025 = mean_squared_error(true_2025, pred_2025)
rmse_2025 = np.sqrt(mse_2025)
r2_2025 = r2_score(true_2025, pred_2025)

# Display metrics for each year
print(f"Metrics for 2023: MAE: {mae_2023:.4f}, MSE: {mse_2023:.4f}, RMSE: {rmse_2023:.4f}, R²: {r2_2023:.4f}")
print(f"Metrics for 2024: MAE: {mae_2024:.4f}, MSE: {mse_2024:.4f}, RMSE: {rmse_2024:.4f}, R²: {r2_2024:.4f}")
print(f"Metrics for 2025: MAE: {mae_2025:.4f}, MSE: {mse_2025:.4f}, RMSE: {rmse_2025:.4f}, R²: {r2_2025:.4f}")

Epoch 1/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 5s 5s/step - loss: 0.6277 - val_loss: 0.6566
Epoch 2/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 81ms/step - loss: 0.6266 - val_loss: 0.6546
Epoch 3/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 84ms/step - loss: 0.6252 - val_loss: 0.6527
Epoch 4/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step - loss: 0.6238 - val_loss: 0.6507
Epoch 5/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 84ms/step - loss: 0.6228 - val_loss: 0.6488
Epoch 6/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 87ms/step - loss: 0.6215 - val_loss: 0.6468
Epoch 7/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step - loss: 0.6203 - val_loss: 0.6448
Epoch 8/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 88ms/step - loss: 0.6189 - val_loss: 0.6428
Epoch 9/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 84ms/step - loss: 0.6178 - val_loss: 0.6409
Epoch 10/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 0.6166 - val_loss: 0.6389
Epoch 11/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - loss: 0.6151 - val_loss: 0.6370
Epoch 12/200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 82ms/step - loss: 0.6142 - val_los